In [9]:
!pip install ipywidgets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.3/2.3 MB 35.0 MB/s eta 0:00:00


In [1]:
!pip install python-Levenshtein

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 36.7 MB/s eta 0:00:00


In [ ]:
!pip install transformers datasets peft accelerate bitsandbytes
# !pip install -U bitsandbytes

### Use Validation Set for zero-shot learning, Train Set for fine-tuning

In [1]:
import json

with open('Annotations/val_v1.0_withQT.json') as f:
  data = json.load(f)


import pandas as pd

pd.set_option('display.max_colwidth', None)

df = pd.DataFrame(data['data'])
# df.head()

In [2]:
root_dir_ocr = "OCR/"
def load_ocr_json(root_dir_ocr):
    with open(root_dir_ocr, 'r') as f:
        return json.load(f)

def extract_text_from_ocr(ocr_json):
    recognition_results = ocr_json.get('recognitionResults', [])
    all_lines = []
    for result in recognition_results:
        lines = result.get('lines', [])
        for line in lines:
            text_line = line.get('text', '')
            all_lines.append(text_line)
    # Join all lines into one string, with newlines between them.
    return "\n".join(all_lines)

def extract_text_from_ocr_sorted(ocr_json):
    recognition_results = ocr_json.get('recognitionResults', [])
    all_lines = []
    for result in recognition_results:
        lines = result.get('lines', [])
        # Sort by the y-coordinate (second value in boundingBox)
        # sorted_lines = sorted(lines, key=lambda line: line.get('boundingBox', [0, 0])[1])
        # for line in sorted_lines:
        for line in lines:
            text_line = line.get('text', '')
            all_lines.append(text_line)
    return "\n".join(all_lines)

# And you have a function that maps the image path to its OCR JSON file path
def extract_and_add_ocr_text(row):
    ocr_path = root_dir_ocr + row['ucsf_document_id'] + "_" + row['ucsf_document_page_no'] + ".json"
    # print(ocr_path)
    try:
        ocr_json = load_ocr_json(ocr_path)
        # Use sorted extraction if needed; otherwise, use extract_text_from_ocr
        ocr_text = extract_text_from_ocr_sorted(ocr_json)
    except Exception as e:
        ocr_text = ""
        print(f"Error processing {ocr_path}: {e}")
    return ocr_text

# Create a new column with OCR text
df['ocr_text'] = df.apply(extract_and_add_ocr_text, axis=1)

display(df[["ocr_text", "question", "answers"]].head(2))

ocr_text  \
0                                                                                              FIGURE C. 2.\nAGE ADJUSTED MOTOR VEHICLE ACCIDENT MORTALITY RATE\n0.3\nCANADA\n8.28\n8.26\n8.24\n8.22\n0.2\n1958\n1955\n1968\n1965\n1978\n1975\n1980\nD. ACTUAL\nMULTIVARIATE PREDICTOR   
1  UNIVERSITY OF CALIFORNIA, SAN DIEGO\nTo\nDate\nTime\nWHILE YOU WERE OUT\nMr.\nMs.\nFrom\nTelephoned\nJasips Clinic\n[ Will phone again\n[.Please phone\nOCame to see you\n[] Will come again\nJRush\nMESSAGE\nTaken by\n"Barce https://www.industrydocuments.ucsf.edu/docs/nkbl0226   

                                                     question  \
0  What is the ‘actual’ value per 1000, during the year 1975?   
1                                 What is name of university?   

                                                                                     answers  
0                                                                                     [0.28]  
1  [university of california, University of California, university of california, san diego]

In [1]:
import pandas as pd

# df = pd.read_csv('val_dataset_add_vlm_ocr.csv')
# display(df[["vlm_ocr_text", "question", "answers"]].head(2))

#df = pd.read_csv('val_dataset_add_spatial_ocr.csv')
# df = pd.read_csv('val_dataset_add_spatial_ocr_and_bounding_box_1.csv')
df = pd.read_csv('val_dataset_add_image_ocr.csv')
# display(df[["vlm_ocr_text", "question", "answers"]].head(2))
# df.info()

In [2]:
df.columns

Index(['questionId', 'question', 'question_types', 'image', 'docId',
       'ucsf_document_id', 'ucsf_document_page_no', 'answers', 'data_split',
       'ocr_text', 'structured_ocr_text'],
      dtype='object')

Zero- shot learning with T5-xl (3B)

In [2]:
import torch
import gc

# Delete the model
# del model
# del tokenizer

# Clear GPU cache
torch.cuda.empty_cache()

# Run garbage collection
gc.collect()

20

In [6]:
from huggingface_hub import login

# Login to Hugging Face
login()

from transformers import AutoTokenizer, AutoModelForSeq2SeqLM

tokenizer = AutoTokenizer.from_pretrained("google/flan-t5-xl")
model = AutoModelForSeq2SeqLM.from_pretrained("google/flan-t5-xl")
model.to("cuda")

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

T5ForConditionalGeneration(
  (shared): Embedding(32128, 2048)
  (encoder): T5Stack(
    (embed_tokens): Embedding(32128, 2048)
    (block): ModuleList(
      (0): T5Block(
        (layer): ModuleList(
          (0): T5LayerSelfAttention(
            (SelfAttention): T5Attention(
              (q): Linear(in_features=2048, out_features=2048, bias=False)
              (k): Linear(in_features=2048, out_features=2048, bias=False)
              (v): Linear(in_features=2048, out_features=2048, bias=False)
              (o): Linear(in_features=2048, out_features=2048, bias=False)
              (relative_attention_bias): Embedding(32, 32)
            )
            (layer_norm): T5LayerNorm()
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (1): T5LayerFF(
            (DenseReluDense): T5DenseGatedActDense(
              (wi_0): Linear(in_features=2048, out_features=5120, bias=False)
              (wi_1): Linear(in_features=2048, out_features=5120, bias=False)
       

In [7]:
def get_answer(spatial_ocr, question, max_length=50):
    # Create the prompt
    prompt = f"Document: {spatial_ocr}\nQuestion: {question}\nAnswer:"
    
    # Tokenize the prompt
    inputs = tokenizer(prompt, return_tensors="pt", padding=True)
    
    # Move all inputs to the same device as the model
    device = model.device
    inputs = {k: v.to(device) for k, v in inputs.items()}
    
    # Generate the answer
    outputs = model.generate(
        **inputs,
        max_length=max_length,
        num_beams=4,
        early_stopping=True
    )
    
    # Decode the answer
    answer = tokenizer.decode(outputs[0], skip_special_tokens=True)
    
    # Return only the answer part, not including the prompt
    answer = answer.replace(prompt, "").strip()
    return answer

df['generated_answer'] = df.apply(lambda row: get_answer(row['spatial_ocr'], row['question']), axis=1)
display(df.head(3))

Token indices sequence length is longer than the specified maximum sequence length for this model (589 > 512). Running this sequence through the model will result in indexing errors


questionId                                           question  \
0       49153  What is the ‘actual’ value per 1000, during th...   
1       24580                        What is name of university?   
2       57349                   What is the name of the company?   

       question_types                      image  docId ucsf_document_id  \
0  ['figure/diagram']  documents/pybv0228_81.png  14465         pybv0228   
1          ['others']   documents/nkbl0226_1.png   7027         nkbl0226   
2          ['layout']  documents/snbx0223_22.png   4733         snbx0223   

   ucsf_document_page_no                                            answers  \
0                     81                                           ['0.28']   
1                      1  ['university of california', 'University of Ca...   
2                     22                     ['itc limited', 'ITC Limited']   

  data_split                                           ocr_text  \
0        val  FIGURE C. 2.\r\nAGE ADJUSTED MOTOR VEHICLE ACC...   
1        val  UNIVERSITY OF CALIFORNIA, SAN DIEGO\r\nTo\r\nD...   
2        val  ITC Limited REPORT AND ACCOUNTS 2013\r\nITC's ...   

                                         spatial_ocr  \
0                                             FIG...   
1  UNIVERSITY OF CALIFORNIA, SAN DIEGO\r\n\r\n To...   
2  ITC Limited REPORT AND ACCOUNTS 2013\r\nITC's ...   

                      generated_answer  
0                                 8.28  
1  University of California, San Diego  
2                          ITC Limited

In [1]:
import os 

filename = "val_dataset_spatial_ocr_t5-xl_answers.csv"
filepath = os.path.join(os.getcwd(), filename)
df.to_csv(filepath, index=False)

NameError: name 'df' is not defined

In [24]:
df = pd.read_csv("val_dataset_add_vlm_ocr_t5-xl_answers.csv")

In [25]:
import ast

# Convert the 'answers' column from string representation to actual lists,
# if needed.
df["answers"] = df["answers"].apply(lambda x: ast.literal_eval(x) if isinstance(x, str) else x)

Evaluation with ANLS (for ocr text generated by mPLUG, then fed to T5-xl)

In [10]:
import re
import string
import Levenshtein

def clean_string(s):
    """
    Lowercase the string, strip it, collapse multiple whitespace into a single space,
    and remove punctuation.
    """
    if s is None:
        return ""
    s = str(s).lower().strip()
    s = re.sub(r'\s+', ' ', s)  # collapse whitespace
    translator = str.maketrans('', '', string.punctuation)
    s = s.translate(translator)
    return s

def normalize_number(token):
    """
    Convert a token to its canonical digit string representation.
    For example, "three" becomes "3" and "3" remains "3".
    Extend the mapping as needed.
    """
    # Try to convert to an integer directly (handles digit strings)
    try:
        val = int(token)
        return str(val)
    except ValueError:
        pass

    # Mapping for numbers as words (extend this mapping as needed)
    mapping = {
        "zero": "0",
        "one": "1",
        "two": "2",
        "three": "3",
        "four": "4",
        "five": "5",
        "six": "6",
        "seven": "7",
        "eight": "8",
        "nine": "9",
        "ten": "10"
        # Add more if needed
    }
    token = token.lower().strip()
    return mapping.get(token, token)

def normalized_levenshtein_similarity(s1, s2):
    """
    If s1 or s2 is a list, compute the similarity for each element and return the maximum.
    Otherwise, clean the strings and then check if one of the strings is purely numeric.
    If one is purely numeric and the other contains a token that matches numerically, return 1.
    Otherwise, return the Levenshtein ratio of the cleaned strings.
    """
    # If either input is a list, compare each element separately.
    if isinstance(s1, list):
        return max([normalized_levenshtein_similarity(item, s2) for item in s1])
    if isinstance(s2, list):
        return max([normalized_levenshtein_similarity(s1, item) for item in s2])
    
    s1_clean = clean_string(s1)
    s2_clean = clean_string(s2)
    
    # If one string is purely digits, try matching a token in the other.
    if s1_clean.isdigit():
        tokens = s2_clean.split()
        for token in tokens:
            if normalize_number(token) == s1_clean:
                return 1.0
    if s2_clean.isdigit():
        tokens = s1_clean.split()
        for token in tokens:
            if normalize_number(token) == s2_clean:
                return 1.0

    # Otherwise, return the Levenshtein ratio.
    return Levenshtein.ratio(s1_clean, s2_clean)

# Row-level similarity: given a row where row['answers'] is a list (or a string) and 
# row['generated_answer'] is the generated OCR output, compute the maximum similarity.
def row_similarity(row):
    ground_truths = row['answers']
    generated = row['generated_answer']
    # Ensure ground_truths is a list.
    if not isinstance(ground_truths, list):
        ground_truths = [ground_truths]
    similarities = [normalized_levenshtein_similarity(gt, generated) for gt in ground_truths]
    return max(similarities) if similarities else 0.0

# --- Applying to a DataFrame ---
# Assuming your DataFrame `df` has columns 'answers' and 'generated_answer'
df["similarity"] = df.apply(row_similarity, axis=1)
ansl_accuracy = df["similarity"].mean()
print("Average similarity:", ansl_accuracy)


Average similarity: 0.6436922991391649


Evaluation with ANLS (original version)

In [9]:
import Levenshtein

# function to compute normalized Levenshtein similarity
def normalized_levenshtein_similarity(s1, s2):
    # If the input is a list, join its elements into a string.
    if isinstance(s1, list):
        s1 = " ".join(map(str, s1))
    if isinstance(s2, list):
        s2 = " ".join(map(str, s2))
        
    # Convert to string, lowercase, and remove surrounding whitespace.
    s1 = str(s1).lower().strip()
    s2 = str(s2).lower().strip()
    
    dist = Levenshtein.distance(s1, s2)
    max_len = max(len(s1), len(s2))
    if max_len == 0:
        return 1.0
    return 1 - (dist / max_len)

# Function to compute the similarity for a single row
def row_similarity(row):
    # Assume row['answers'] is a list of ground-truth strings
    ground_truths = row['answers']
    generated = row['generated_answer']
    # Compute similarity with each ground truth answer
    similarities = [normalized_levenshtein_similarity(gt, generated) for gt in ground_truths]
    # We take the maximum similarity (best match) as the score for that row.
    return max(similarities) if similarities else 0.0


# Compute similarity for each row
df["similarity"] = df.apply(row_similarity, axis=1)

# Calculate the average similarity (ANSL)
ansl_accuracy = df["similarity"].mean()

print("Row similarities:")
print(df[["answers", "generated_answer", "similarity"]])
print("Average Normalized Levenshtein Similarity (ANSL):", ansl_accuracy)

Row similarities:
                                                answers  \
0                                              ['0.28']   
1     ['university of california', 'University of Ca...   
2                        ['itc limited', 'ITC Limited']   
3                            ['san diego', 'San Diego']   
4                                              ['Paul']   
...                                                 ...   
5344             ['Raymond C. Guth', 'Raymond c. Guth']   
5345  ['Age adjusted motor vehicle accident mortalit...   
5346  ['age adjusted motor vehicle accident mortalit...   
5347                                           ['1980']   
5348                                           ['0.24']   

                           generated_answer  similarity  
0                                      8.28    0.250000  
1       University of California, San Diego    0.028571  
2                               ITC Limited    0.090909  
3                                 SAN DIE

In [11]:
non_nan_count = df["generated_answer"].count()
print(f"Non-NaN count in '{"generated_answer"}': {non_nan_count}", len(df))


Non-NaN count in 'generated_answer': 5349 5349


Check the generated answers with low similarity scores

In [29]:
display(df[df["similarity"]<0.5][["answers", "generated_answer", "similarity"]].iloc[40:60])

answers  \
90   [Steering Committee Meeting, Steering committe...   
91   [Volunteers Against Hunger Steering Committee,...   
92   [Bert Shulimson, Bert Shulimson , Executive Se...   
95                                [candyman, Candyman]   
96                              [available, Available]   
97                                    [wanted, Wanted]   
98   [independent ice and cold storage co., Indepen...   
101              [10:00 - 11:30 AM, 10:00 -  11:30 AM]   
102                 [ronald f. meyer, Ronald F. Meyer]   
103                                     [609/924-6648]   
108                                    [bingo, Bingo!]   
111                                              [723]   
112                               [candyman, Candyman]   
113                               [projects, Projects]   
115                               [candyman, Candyman]   
118                                 [Sunfeast Yippee!]   
119           [mint-o Ultra mintz, mint-o Ultra Mintz]   
120                                   [Fiama Di Wills]   
124                         [Dream Cream, Dream cream]   
125            [Carol A. Tozzi, Ph.D., Carol A. Tozzi]   

                                generated_answer  similarity  
90   The Missouri Association for Social Welfare    0.318841  
91                       Mrs. Gideon H. Schiller    0.400000  
92                            GIDEON H. SCHILLER    0.346154  
95                                        BINGO!    0.153846  
96                             NAMES IN THE NEWS    0.230769  
97                             NAMES IN THE NEWS    0.347826  
98                   Lewis Refrigeration Company    0.322581  
101                                June 13, 2001    0.320000  
102                             ESEQUIEL GRANADO    0.266667  
103                                       555-6B    0.133333  
108                                Merely Temple    0.000000  
111                                          $ 0    0.000000  
112                                       Bingo!    0.153846  
113                            Swanson Interests    0.320000  
115                                       Bingo!    0.153846  
118                              Aashirvaad Atta    0.200000  
119                                          d).    0.000000  
120                                     Candyman    0.272727  
124                                       Snacky    0.235294  
125                                       Yvonne    0.105263

### Fine-tune on DocVQA with T5

In [5]:
from datasets import Dataset
from transformers import (
    AutoTokenizer, 
    AutoModelForSeq2SeqLM, 
    DataCollatorForSeq2Seq, 
    Seq2SeqTrainingArguments, 
    Seq2SeqTrainer
)
from peft import get_peft_model, LoraConfig, TaskType
import torch

# Load the tokenizer and model
tokenizer = AutoTokenizer.from_pretrained("google/flan-t5-xl")
model = AutoModelForSeq2SeqLM.from_pretrained("google/flan-t5-xl",
                                              device_map="auto",
                                              load_in_8bit=True)
                                            #   torch_dtype=torch.floats16)

peft_config = LoraConfig(
    r=8,
    lora_alpha=32,
    target_modules=["q", "v"],
    lora_dropout=0.1,
    bias="none",
    task_type=TaskType.SEQ_2_SEQ_LM
)

model = get_peft_model(model, peft_config)
model.print_trainable_parameters()

The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

trainable params: 4,718,592 || all params: 2,854,475,776 || trainable%: 0.1653


In [9]:
def preprocess_function(examples):
    # Create the prompt combining the OCR text and the question.
    inputs = [
        f"Document: {doc}\nQuestion: {question}\nAnswer:" 
        for doc, question in zip(examples["ocr_text"], examples["question"])
    ]
    model_inputs = tokenizer(inputs, max_length=512, truncation=True)
    
    # Use the first answer in the list as the training target.
    # (You could also randomly choose one if desired.)
    targets = [ans[0] if isinstance(ans, list) else ans for ans in examples["answers"]]
    with tokenizer.as_target_tokenizer():
        labels = tokenizer(targets, max_length=128, truncation=True)
    model_inputs["labels"] = labels["input_ids"]
    
    # Optionally, keep the full answers in the dataset for evaluation purposes.
    model_inputs["all_answers"] = examples["answers"]
    model_inputs["target_text"] = targets
    return model_inputs

# Convert the DataFrame to a Hugging Face Dataset and tokenize it.
dataset = Dataset.from_pandas(df)
tokenized_dataset = dataset.map(preprocess_function, batched=True)

# Optionally split into training and evaluation sets.
split_dataset = tokenized_dataset.train_test_split(test_size=0.1)
train_dataset = split_dataset["train"]
eval_dataset = split_dataset["test"]

# Data collator to dynamically pad inputs/labels.
data_collator = DataCollatorForSeq2Seq(tokenizer, model=model)

Map:   0%|          | 0/5349 [00:00<?, ? examples/s]

/home/cheng-ubuntu/anaconda3/envs/torch180/lib/python3.13/site-packages/transformers/tokenization_utils_base.py:3980: UserWarning: `as_target_tokenizer` is deprecated and will be removed in v5 of Transformers. You can tokenize your labels by using the argument `text_target` of the regular `__call__` method (either in the same call as your input texts if you use the same keyword arguments, or in a separate call.
  warnings.warn(


In [12]:
import difflib
import numpy as np

# Define a simple similarity function using difflib.
def is_similar(pred, target, threshold=0.8):
    return difflib.SequenceMatcher(None, pred.lower(), target.lower()).ratio() > threshold

# Custom metric: checks if the generated answer is similar to the target answer.
# Here we compare to the first answer (stored in "target_text") used during training.
def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    
    # Replace -100 in predictions and labels with the pad token id
    predictions = np.where(predictions == -100, tokenizer.pad_token_id, predictions)
    labels = np.where(labels == -100, tokenizer.pad_token_id, labels)
    
    decoded_preds = tokenizer.batch_decode(predictions, skip_special_tokens=True)
    decoded_labels = tokenizer.batch_decode(labels, skip_special_tokens=True)
    
    correct = 0
    for pred, label in zip(decoded_preds, decoded_labels):
        if is_similar(pred.strip(), label.strip()):
            correct += 1
    accuracy = correct / len(decoded_preds)
    return {"accuracy": accuracy}

# Define training arguments.
training_args = Seq2SeqTrainingArguments(
    output_dir="./t5_docvqa_finetuned",
    evaluation_strategy="epoch",
    learning_rate=5e-4,
    per_device_train_batch_size=4,
    per_device_eval_batch_size=4,
    weight_decay=0.01,
    save_total_limit=3,
    num_train_epochs=3,
    predict_with_generate=True,
    fp16=True
)

# Initialize the Trainer.
trainer = Seq2SeqTrainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=eval_dataset,
    tokenizer=tokenizer,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
)

# Start fine-tuning.
trainer.train()

/home/cheng-ubuntu/anaconda3/envs/torch180/lib/python3.13/site-packages/transformers/training_args.py:1611: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/tmp/ipykernel_552512/1097309842.py:42: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Seq2SeqTrainer.__init__`. Use `processing_class` instead.
  trainer = Seq2SeqTrainer(
No label_names provided for model class `PeftModelForSeq2SeqLM`. Since `PeftModel` hides base models input arguments, if label_names is not given, label_names can't be set automatically within `Trainer`. Note that empty label_names list will be used instead.


TrainOutput(global_step=3612, training_loss=5.692503564777565, metrics={'train_runtime': 1662.9312, 'train_samples_per_second': 8.685, 'train_steps_per_second': 2.172, 'total_flos': 1.160966248735703e+17, 'train_loss': 5.692503564777565, 'epoch': 3.0})

### mistral

In [11]:
import torch
import gc

# Delete the model
# del model_llama
# del model
del tokenizer
del model_mistral

# Clear GPU cache
torch.cuda.empty_cache()

# Run garbage collection
gc.collect()

1156

In [3]:
from transformers import AutoTokenizer, AutoModelForCausalLM
from huggingface_hub import login

# Login to Hugging Face
login()
model_mistral_id = "mistralai/Mistral-7B-Instruct-v0.3"

tokenizer = AutoTokenizer.from_pretrained(model_mistral_id)
model_mistral = AutoModelForCausalLM.from_pretrained(
    model_mistral_id,
    torch_dtype="bfloat16",  # or torch.float16
    # device_map="auto"
    device_map={"": 0}
)
# model_mistral.to("cuda")
# model_mistral.eval()

Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

In [4]:
model_mistral.eval()

# Positive in-context example to show the desired answer style.
POSITIVE_EXAMPLE = """<s>[INST]
**Positive Example:**

**Question:**  
What is the ‘actual’ value per 1000, during the year 1975?

**Document Content (spatial_ocr):**  
FIGURE C. 2.

AGE ADJUSTED MOTOR VEHICLE ACCIDENT MORTALITY RATE  
CANADA  
0.3

8.28  
8.26  
8.24  
8.22

0.2

1958 1955 1968 1965 1978 1975 1980

D. ACTUAL  
MULTIVARIATE PREDICTOR

**Concise Answer:**  
0.28
[/INST]"""

def format_prompt(spatial_ocr, question):
    """
    Builds the prompt by including a positive example and then the new query.
    The new query instructs the model to answer concisely (i.e., provide only the brief answer).
    """
    return f"""{POSITIVE_EXAMPLE}

<s>[INST] You are a helpful assistant. Based on the document text below, answer the question in a concise manner 
(i.e., provide only a brief answer, not a full sentence).

Document:
{spatial_ocr}

Question:
{question}

**Concise Answer:**
[/INST]
"""

# Run inference on the generated prompt
def generate_answer(prompt, max_new_tokens=50):
    inputs = tokenizer(prompt, return_tensors="pt").to(model_mistral.device)
    with torch.no_grad():
        outputs = model_mistral.generate(**inputs, max_new_tokens=max_new_tokens)
    # Decode and extract the answer after the closing tag
    result = tokenizer.decode(outputs[0], skip_special_tokens=True).split('[/INST]')[-1].strip()
    # print(result)
    return result

# Apply to your DataFrame: assuming 'spatial_ocr' and 'question' columns exist in df
df["generated_answer"] = df.apply(lambda row: generate_answer(format_prompt(row["structured_ocr_text"], row["question"])), axis=1)

Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for o

In [ ]:
# model_mistral.eval()

# def format_prompt(spatial_ocr, question):
#     return f"""<s>[INST] You are a helpful assistant. Based on the document text below, answer the question.

# Document:
# {spatial_ocr}

# Question:
# {question}
# [/INST]
# """

# # Run inference
# def generate_answer(prompt, max_new_tokens=50):
#     inputs = tokenizer(prompt, return_tensors="pt").to(model_mistral.device)
#     with torch.no_grad():
#         outputs = model_mistral.generate(**inputs, max_new_tokens=max_new_tokens)
#     return tokenizer.decode(outputs[0], skip_special_tokens=True).split('[/INST]')[-1].strip()

# # Apply to DataFrame
# df["generated_answer"] = df.apply(lambda row: generate_answer(format_prompt(row["spatial_ocr"], row["question"])), axis=1)

# # Display results
# # print(df[["ocr_text", "question", "generated_answer"]])
# display(df.head(3))

Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:2 for o

questionId                                           question  \
0       49153  What is the ‘actual’ value per 1000, during th...   
1       24580                        What is name of university?   
2       57349                   What is the name of the company?   

       question_types                      image  docId ucsf_document_id  \
0  ['figure/diagram']  documents/pybv0228_81.png  14465         pybv0228   
1          ['others']   documents/nkbl0226_1.png   7027         nkbl0226   
2          ['layout']  documents/snbx0223_22.png   4733         snbx0223   

   ucsf_document_page_no                                            answers  \
0                     81                                           ['0.28']   
1                      1  ['university of california', 'University of Ca...   
2                     22                     ['itc limited', 'ITC Limited']   

  data_split                                           ocr_text  \
0        val  FIGURE C. 2.\r\nAGE ADJUSTED MOTOR VEHICLE ACC...   
1        val  UNIVERSITY OF CALIFORNIA, SAN DIEGO\r\nTo\r\nD...   
2        val  ITC Limited REPORT AND ACCOUNTS 2013\r\nITC's ...   

                                         spatial_ocr  \
0                                             FIG...   
1  UNIVERSITY OF CALIFORNIA, SAN DIEGO\r\n\r\n To...   
2  ITC Limited REPORT AND ACCOUNTS 2013\r\nITC's ...   

                                    generated_answer  
0  You are a helpful assistant. Based on the docu...  
1  You are a helpful assistant. Based on the docu...  
2  You are a helpful assistant. Based on the docu...

In [5]:
import os 

filename = "val_dataset_add_vlm_ocr_mistral_answers.csv"
filepath = os.path.join(os.getcwd(), filename)
df.to_csv(filepath, index=False)

In [6]:
pd.set_option('display.max_rows', None)

# To display all columns:
pd.set_option('display.max_columns', None)

# To display the full width of each column (optional, but can be useful for long text):
pd.set_option('display.max_colwidth', None)

# display(df[["question", "answers", "spatial_ocr"]].head(3))
display(df[["generated_answer", "answers"]].head(3))

generated_answer  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   **Positive Example:**\n\n**Question:**  \nWhat is the ‘actual’ value per 1000, during the year 1975?\n\n**Document Content (spatial_ocr):**  \nFIGURE C. 2.\n\nAGE ADJUSTED MOTOR VEHICLE ACCIDENT MORTALITY RATE  \nCANADA  \n0.3\n\n8.28  \n8.26  \n8.24  \n8.22\n\n0.2\n\n1958 1955 1968 1965 1978 1975 1980\n\nD. ACTUAL  \nMULTIVARIATE PREDICTOR\n\n**Concise Answer:**  \n0.28\n\n\n You are a helpful assistant. Based on the document text below, answer the question in a concise manner \n(i.e., provide only a brief answer, not a full sentence).\n\nDocument:\nFIGURE C. 2.  \r\nAGE ADJUSTED MOTOR VEHICLE ACCIDENT MORTALITY RATE  \r\nCANADA  \r\n0.3  \r\n0.28  \r\n0.26  \r\n0.24  \r\n0.22  \r\n0.2  \r\nPER  \r\n1000  \r\n1950  \r\n1955  \r\n1960  \r\n1965  \r\n1970  \r\n1975  \r\n1980  \r\nD. ACTUAL  \r\nMULTIVARIATE PREDICTOR  \r\nACTUAL  \r\nMULTIVARIATE PREDICTOR  \n\nQuestion:\nWhat is the ‘actual’ value per 1000, during the year 1975?\n\n**Concise Answer:**\n\n0.28   
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            **Positive Example:**\n\n**Question:**  \nWhat is the ‘actual’ value per 1000, during the year 1975?\n\n**Document Content (spatial_ocr):**  \nFIGURE C. 2.\n\nAGE ADJUSTED MOTOR VEHICLE ACCIDENT MORTALITY RATE  \nCANADA  \n0.3\n\n8.28  \n8.26  \n8.24  \n8.22\n\n0.2\n\n1958 1955 1968 1965 1978 1975 1980\n\nD. ACTUAL  \nMULTIVARIATE PREDICTOR\n\n**Concise Answer:**  \n0.28\n\n\n You are a helpful assistant. Based on the document text below, answer the question in a concise manner \n(i.e., provide only a brief answer, not a full sentence).\n\nDocument:\nUNIVERSITY OF CALIFORNIA, SAN DIEGO  \r\nTo  \r\nPaul  \r\nDate  \r\n11/30/03  \r\nTime  \r\n2:04 PM  \r\n\r\nWHILE YOU WERE OUT  \r\nMr.  \r\nMs.  \r\nFrom  \r\nWilson 455-8056  \r\nScripps Clinic  \r\n[ ] Telephoned  \r\n[ ] Came to see you  \r\n[ ] Will phone again  \r\n[ ] Will come again  \r\n[ ] Rush  \r\n\r\nMESSAGE  \r\nRe Program Committee-   \r\ntoday Feb. "It would  \r\nprobably be 1 or 2  \r\nwouldn't work (1903)  \r\nnothing other than better, help.  \r\nPhone party at  \r\nMary  \r\nTaken by  \r\n73875-128  \n\nQuestion:\nWhat is name of university?\n\n**Concise Answer:**\n\nUniversity of California, San Diego   
2  **Positive Example:**\n\n**Question:**  \nWhat is the ‘actual’ value per 1000, during the year 

In [7]:
# Extract text after the final occurrence of "**Concise Answer:**"
df["cleaned_answer"] = df["generated_answer"].apply(
    lambda text: text.rsplit("**Concise Answer:**", 1)[-1].strip()
)

# Optionally, view the result
display(df["cleaned_answer"].head())

0                                   0.28
1    University of California, San Diego
2                            ITC Limited
3    University of California, San Diego
4                                   Paul
Name: cleaned_answer, dtype: object

### Post-processing

In [8]:
import ast

df['answers'] = df['answers'].apply(ast.literal_eval)

In [10]:
import re
import string
import Levenshtein
from rapidfuzz import fuzz

def normalize_text(text):
    # Remove punctuation and extra whitespace, and convert to lower-case
    text = re.sub(r'[^\w\s]', '', text)  # Remove punctuation
    return text.lower().strip()

# Function to calculate similarity between two strings. Here, we use RapidFuzz's fuzz.ratio.
# You can choose a different scoring function (like fuzz.token_set_ratio) if desired.
def calculate_similarity(predicted, candidate):
    # Normalize both strings
    predicted_norm = normalize_text(predicted)
    candidate_norm = normalize_text(candidate)
    # Calculate the similarity ratio (a value between 0 and 100), then convert to a value between 0 and 1.
    ratio = fuzz.ratio(predicted_norm, candidate_norm) / 100.0
    return ratio

# Function to compute the maximum similarity for one row
def max_similarity(row):
    pred = row['cleaned_answer']
    candidates = row['answers']
    # Compute similarity for each candidate and return the maximum
    scores = [calculate_similarity(pred, candidate) for candidate in candidates]
    return max(scores)

# Apply the function to compute the new similarity score for each row
df['max_similarity'] = df.apply(max_similarity, axis=1)
# --- Applying to a DataFrame ---
# Assuming your DataFrame `df` has columns 'answers' and 'predicted_answer'
# df["similarity"] = df.apply(row_similarity, axis=1)
ansl_accuracy = df["max_similarity"].mean()
print("Average similarity:", ansl_accuracy)

Average similarity: 0.7640549014874796


In [21]:
import Levenshtein

def normalize(text):
    return str(text).lower().strip()

def normalized_levenshtein_similarity(s1, s2):
    s1, s2 = normalize(s1), normalize(s2)
    dist = Levenshtein.distance(s1, s2)
    max_len = max(len(s1), len(s2))
    if max_len == 0:
        return 1.0
    return 1 - (dist / max_len)

def row_similarity(row):
    predicted = normalize(row["predicted_answer"])
    ground_truths = [normalize(ans) for ans in row["answers"]]

    # # Check if any answer is contained in predicted
    # for gt in ground_truths:
    #     if gt in predicted:
    #         return 1.0

    # Else, compute max Levenshtein similarity
    similarities = [normalized_levenshtein_similarity(gt, predicted) for gt in ground_truths]
    return max(similarities) if similarities else 0.0

# Apply to DataFrame
df["similarity"] = df.apply(row_similarity, axis=1)
ansl_accuracy = df["similarity"].mean()

print("Row similarities:")
print(df[["answers", "predicted_answer", "similarity"]])
print("Average Normalized Levenshtein Similarity (ANSL):", ansl_accuracy)

Row similarities:
                                                                                                                                                                                                                                                                                                                                                                                                      answers  \
0                                                                                                                                                                                                                                                                                                                                                                                                    ['0.28']   
1                                                                                                                                                                                   

In [13]:
df[df["max_similarity"]<0.5][["answers", "cleaned_answer", "max_similarity"]].head(20)

answers  \
0                                    [0.28]   
3                    [san diego, San Diego]   
4                                    [Paul]   
11             [dark fantasy, Dark fantasy]   
13                                      [2]   
16                                      [6]   
17                                      [6]   
29                                     [31]   
37                                [70%, 70]   
39                                [57, 57%]   
54                                     [29]   
56  [Scissors Menthol Fresh, Menthol Fresh]   
64                               [seven, 7]   
66                                     [40]   
67                                     [30]   
68                                      [5]   
69                                   [33.0]   
72                 [FOUR WEEKS, four weeks]   
75                 [BASAL DIET, basal diet]   
78                               [itc, ITC]   

                                                                                                                                                                    cleaned_answer  \
0                                                                                                                                                                   0.2 (per 1000)   
3                                                                                                                                              University of California, San Diego   
4                                                                                                                                                         Mr. or Ms. Jasips Clinic   
11                                                                                                                                                                      Choco Fill   
13                                                                                                                                                                               3   
16                                                                                                                                                   2 (A. Baijal and S. Banerjee)   
17                                                                                                                                                                               5   
29                                                                                                                                                                      51336 9541   
37                                                                                                                                                                              64   
39                                                                                                                                                                              61   
54                                                                                                                                                                      51336 9882   
56  Scissors has not been explicitly mentioned as being launched in Tamil Nadu in the provided document. It has only been mentioned as being launched in Uttar Pradesh and Kerala.   
64                                                                                                                                                                      7 children   
66                                                                                                                                                                         40 days   
67                                                                                                                                                                         30 days   
68                                                                                                                                      

### Fine-tune on DocVQA

In [5]:
from datasets import Dataset

def format_instruction(row):
    return f"<s>[INST] You are a helpful assistant. Based on the document text below, answer the question.\n\nDocument:\n{row['ocr_text']}\n\nQuestion:\n{row['question']} [/INST] {row['answers'][0]}</s>"

# Use the first answer in the list as target
df["formatted"] = df.apply(format_instruction, axis=1)

# Convert to HuggingFace Dataset
dataset = Dataset.from_pandas(df[["formatted"]])

In [10]:
from transformers import AutoTokenizer

model_id_mistral = "mistralai/Mistral-7B-Instruct-v0.3"
tokenizer = AutoTokenizer.from_pretrained(model_id_mistral, trust_remote_code=True)
tokenizer.pad_token = tokenizer.eos_token

def tokenize(batch):
    return tokenizer(
        batch["formatted"],
        truncation=True,
        padding="max_length",
        max_length=1024,
    )

tokenized_dataset = dataset.map(tokenize, batched=True)
tokenized_dataset = tokenized_dataset.map(lambda x: {"labels": x["input_ids"]})

Map:   0%|          | 0/5349 [00:00<?, ? examples/s]

Map:   0%|          | 0/5349 [00:00<?, ? examples/s]

In [7]:
from transformers import AutoModelForCausalLM, TrainingArguments, Trainer
from peft import LoraConfig, get_peft_model, TaskType

model_mistral = AutoModelForCausalLM.from_pretrained(
    model_id_mistral,
    load_in_4bit=True,
    device_map="auto",
    torch_dtype="bfloat16"
)

peft_config = LoraConfig(
    r=8,
    lora_alpha=16,
    target_modules=["q_proj", "v_proj", "k_proj", "o_proj"],  # safe bet for Mistral
    lora_dropout=0.1,
    bias="none",
    task_type=TaskType.CAUSAL_LM
)

model_mistral = get_peft_model(model_mistral, peft_config)

The `load_in_4bit` and `load_in_8bit` arguments are deprecated and will be removed in the future versions. Please, pass a `BitsAndBytesConfig` object in `quantization_config` argument instead.


Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

In [8]:
training_args = TrainingArguments(
    output_dir="./mistral-finetuned",
    per_device_train_batch_size=1,
    gradient_accumulation_steps=4,
    learning_rate=2e-5,
    num_train_epochs=3,
    fp16=True,
    logging_steps=10,
    save_steps=100,
    save_total_limit=2,
    report_to="none"
)

In [11]:
trainer = Trainer(
    model=model_mistral,
    args=training_args,
    train_dataset=tokenized_dataset,
    tokenizer=tokenizer
)

trainer.train()

/tmp/ipykernel_366509/2108063812.py:1: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(
No label_names provided for model class `PeftModelForCausalLM`. Since `PeftModel` hides base models input arguments, if label_names is not given, label_names can't be set automatically within `Trainer`. Note that empty label_names list will be used instead.


OutOfMemoryError: CUDA out of memory. Tried to allocate 224.00 MiB. GPU 0 has a total capacity of 23.63 GiB of which 210.31 MiB is free. Including non-PyTorch memory, this process has 22.91 GiB memory in use. Of the allocated memory 22.24 GiB is allocated by PyTorch, and 225.49 MiB is reserved by PyTorch but unallocated. If reserved but unallocated memory is large try setting PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True to avoid fragmentation.  See documentation for Memory Management  (https://pytorch.org/docs/stable/notes/cuda.html#environment-variables)

Zero-shot learning with LLaMa 3.2 - 3B - Instruct

In [3]:
from huggingface_hub import login

# Login to Hugging Face
login()

from transformers import AutoTokenizer, AutoModelForCausalLM
import torch
import gc

# Clear GPU cache
torch.cuda.empty_cache()
gc.collect()

tokenizer_llama = AutoTokenizer.from_pretrained("meta-llama/Llama-3.2-3B-Instruct")
model_llama = AutoModelForCausalLM.from_pretrained("meta-llama/Llama-3.2-3B-Instruct")
model_llama.to("cuda")

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

LlamaForCausalLM(
  (model): LlamaModel(
    (embed_tokens): Embedding(128256, 3072)
    (layers): ModuleList(
      (0-27): 28 x LlamaDecoderLayer(
        (self_attn): LlamaAttention(
          (q_proj): Linear(in_features=3072, out_features=3072, bias=False)
          (k_proj): Linear(in_features=3072, out_features=1024, bias=False)
          (v_proj): Linear(in_features=3072, out_features=1024, bias=False)
          (o_proj): Linear(in_features=3072, out_features=3072, bias=False)
        )
        (mlp): LlamaMLP(
          (gate_proj): Linear(in_features=3072, out_features=8192, bias=False)
          (up_proj): Linear(in_features=3072, out_features=8192, bias=False)
          (down_proj): Linear(in_features=8192, out_features=3072, bias=False)
          (act_fn): SiLU()
        )
        (input_layernorm): LlamaRMSNorm((3072,), eps=1e-05)
        (post_attention_layernorm): LlamaRMSNorm((3072,), eps=1e-05)
      )
    )
    (norm): LlamaRMSNorm((3072,), eps=1e-05)
    (rotary_emb

In [5]:
def get_answer(ocr_text, question, max_length=2200):
    # Create the prompt
    prompt = f"""Document: {ocr_text}

    Question: {question}

    Provide only the exact text answer with no explanation or additional text. Be concise.
    Answer:"""
    
    # Tokenize the prompt
    inputs = tokenizer_llama(prompt, return_tensors="pt")
    
    # Move all inputs to the same device as the model
    device = model_llama.device
    inputs = {k: v.to(device) for k, v in inputs.items()}
    
    # Generate the answer
    outputs = model_llama.generate(
        **inputs,
        max_length=max_length,
        do_sample=True,  # Enable sampling
        temperature=0.7,  # Add some randomness (0.7 is a good value)
        top_p=0.9,  # Use nucleus sampling
        repetition_penalty=1.2,  # Penalize repetition
        no_repeat_ngram_size=3,  # Prevent repeating 3-grams
        num_beams=4,  # Use beam search
        early_stopping=True  # Stop when all beams reach EOS
        )

    answer = tokenizer_llama.decode(outputs[0], skip_special_tokens=True)
    
    # Return only the answer part, not including the prompt
    answer = answer.replace(prompt, "").strip()
    return answer

df['generated_answer'] = df.apply(lambda row: get_answer(row['ocr_text'], row['question']), axis=1)
# display(df.head(3))
# df.loc[:6, 'generated_answer'] = df.iloc[:7].apply(lambda row: get_answer(row['ocr_text'], row['question']), axis=1)
display(df.head(6))

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for

KeyboardInterrupt: 

In [ ]:
import Levenshtein

# function to compute normalized Levenshtein similarity
def normalized_levenshtein_similarity(s1, s2):
    s1, s2 = str(s1).lower().strip(), str(s2).lower().strip()
    dist = Levenshtein.distance(s1, s2)
    max_len = max(len(s1), len(s2))
    if max_len == 0:
        return 1.0
    return 1 - (dist / max_len)

# Function to compute the similarity for a single row
def row_similarity(row):
    # Assume row['answers'] is a list of ground-truth strings
    ground_truths = row['answers']
    generated = row['generated_answer']
    # Compute similarity with each ground truth answer
    similarities = [normalized_levenshtein_similarity(gt, generated) for gt in ground_truths]
    # We take the maximum similarity (best match) as the score for that row.
    return max(similarities) if similarities else 0.0


# Compute similarity for each row
df["similarity"] = df.apply(row_similarity, axis=1)

# Calculate the average similarity (ANSL)
ansl_accuracy = df["similarity"].mean()

print("Row similarities:")
print(df[["answers", "generated_answer", "similarity"]])
print("Average Normalized Levenshtein Similarity (ANSL):", ansl_accuracy)

In [20]:
def build_minimal_fewshot_prompt(examples_df, ocr_text, question, n_examples=2):
    prompt = ""
    # Use the first n_examples from the DataFrame as few-shot examples.
    for i, row in examples_df.head(n_examples).iterrows():
        # Extract the minimal answer (assuming it's the first answer)
        example_answer = row['answers'][0] if isinstance(row['answers'], list) else row['answers']
        prompt += f"Example {i+1}:\n"
        prompt += f"Document: {row['ocr_text']}\n"
        prompt += f"Question: {row['question']}\n"
        prompt += f"Answer: {example_answer}\n\n"
    # Append the test example with a clear signal
    prompt += "Now, answer this:\n"
    prompt += f"Document: {ocr_text}\n"
    prompt += f"Question: {question}\n"
    prompt += "Answer (only provide the direct answer with no extra text):"
    return prompt

def get_answer_with_fewshot(examples_df, ocr_text, question, max_length=2200, n_examples=2):
    # Build the prompt using few-shot examples.
    prompt = build_minimal_fewshot_prompt(examples_df, ocr_text, question, n_examples)
    
    # Tokenize the prompt.
    inputs = tokenizer_llama(prompt, return_tensors="pt")
    
    # Move all inputs to the model's device.
    device = model_llama.device
    inputs = {k: v.to(device) for k, v in inputs.items()}
    
    # Generate the answer.
    outputs = model_llama.generate(
        **inputs,
        max_length=max_length,
        do_sample=True,
        temperature=0.7,
        top_p=0.9,
        repetition_penalty=1.2,
        no_repeat_ngram_size=3,
        num_beams=4,
        early_stopping=True
    )
    
    # Decode the output.
    generated = tokenizer_llama.decode(outputs[0], skip_special_tokens=True)
    
    # Remove the prompt from the generated output (if echoed).
    answer = generated.replace(prompt, "").strip()
    # Alternatively, you could split on a delimiter (e.g., "\n") if needed.
    return answer

example_df = df.head(2)
# df.loc[2:6, 'generated_answer'] = df.iloc[2:7].apply(lambda row: get_answer_with_fewshot(example_df, row['ocr_text'], row['question']), axis=1)
df['generated_answer'] = df.apply(lambda row: get_answer_with_fewshot(example_df, row['ocr_text'], row['question']), axis=1)
display(df.head(6))

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for

KeyboardInterrupt: 

Tried different temperatures and repetition penalty to solve the echo problems

In [13]:
def get_answer(ocr_text, question, max_length=500):
    # Create the prompt
    prompt = f"""Document: {ocr_text}

    Question: {question}

    Provide only the exact text answer with no explanation or additional text. Be concise.
    Answer:"""
    
    # Tokenize the prompt
    inputs = tokenizer_llama(prompt, return_tensors="pt")
    
    # Move all inputs to the same device as the model
    device = model_llama.device
    inputs = {k: v.to(device) for k, v in inputs.items()}
    
    # Generate the answer
    outputs = model_llama.generate(
        **inputs,
        max_length=max_length,
        do_sample=True,  # Enable sampling
        temperature=0.7,  # Add some randomness (0.7 is a good value)
        top_p=0.9,  # Use nucleus sampling
        repetition_penalty=1.2,  # Penalize repetition
        no_repeat_ngram_size=3,  # Prevent repeating 3-grams
        num_beams=4,  # Use beam search
        early_stopping=True  # Stop when all beams reach EOS
        )

    answer = tokenizer_llama.decode(outputs[0], skip_special_tokens=True)
    
    # Return only the answer part, not including the prompt
    answer = answer.replace(prompt, "").strip()
    return answer

# df['generated_answer'] = df.apply(lambda row: get_answer(row['ocr_text'], row['question']), axis=1)
# display(df.head(3))
df.loc[:6, 'generated_answer'] = df.iloc[:7].apply(lambda row: get_answer(row['ocr_text'], row['question']), axis=1)
# df['generated_answer'] = df.apply(lambda row: get_answer(row['ocr_text'], row['question']), axis=1)
display(df.head(6))

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


questionId                                                    question  \
0       49153  What is the ‘actual’ value per 1000, during the year 1975?   
1       24580                                 What is name of university?   
2       57349                            What is the name of the company?   

     question_types                      image  docId ucsf_document_id  \
0  [figure/diagram]  documents/pybv0228_81.png  14465         pybv0228   
1          [others]   documents/nkbl0226_1.png   7027         nkbl0226   
2          [layout]  documents/snbx0223_22.png   4733         snbx0223   

  ucsf_document_page_no  \
0                    81   
1                     1   
2                    22   

                                                                                     answers  \
0                                                                                     [0.28]   
1  [university of california, University of California, university of california, san diego]   
2                                                                 [itc limited, ITC Limited]   

  data_split  \
0        val   
1        val   
2        val   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               ocr_text  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               FIGURE C. 2.\nAGE ADJUSTED MOTOR VEHICLE ACCIDENT MORTALITY RATE\n0.3\nCANADA\n8.28\n8.26\n8.24\n8.22\n0.2\n1958\n1955\n1968\n1965\n1978\n1975\n1980\nD. ACTUAL\nMULTIVARIATE PREDICTOR   
1                                                                                                                                                                                                                                                               

In [15]:
display(df.head(7))

questionId                                                    question  \
0       49153  What is the ‘actual’ value per 1000, during the year 1975?   
1       24580                                 What is name of university?   
2       57349                            What is the name of the company?   
3       24581                           Where is the university located ?   
4       24582                               To whom is the document sent?   
5       39079                          What the location address of NSDA?   
6       57357  What is ITC's brand of Atta featured in the advertisement?   

        question_types                      image  docId ucsf_document_id  \
0     [figure/diagram]  documents/pybv0228_81.png  14465         pybv0228   
1             [others]   documents/nkbl0226_1.png   7027         nkbl0226   
2             [layout]  documents/snbx0223_22.png   4733         snbx0223   
3             [others]   documents/nkbl0226_1.png   7027         nkbl0226   
4  [handwritten, form]   documents/nkbl0226_1.png   7027         nkbl0226   
5             [layout]   documents/qqvf0227_1.png  11190         qqvf0227   
6        [Image/Photo]  documents/snbx0223_22.png   4733         snbx0223   

  ucsf_document_page_no  \
0                    81   
1                     1   
2                    22   
3                     1   
4                     1   
5                     1   
6                    22   

                                                                                                    answers  \
0                                                                                                    [0.28]   
1                 [university of california, University of California, university of california, san diego]   
2                                                                                [itc limited, ITC Limited]   
3                                                                                    [san diego, San Diego]   
4                                                                                                    [Paul]   
5  [1128 SIXTEENTH ST., N. W., WASHINGTON, D. C. 20036, 1128 sixteenth st., N. W., washington, D. C. 20036]   
6                                                                                  [aashirvaad, Aashirvaad]   

  data_split  \
0        val   
1        val   
2        val   
3        val   
4        val   
5        val   
6        val   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               ocr_text  \
0                                                                                                                                                                                                                                                  

Check the generated answers with low similarity scores

In [ ]:
import Levenshtein

# function to compute normalized Levenshtein similarity
def normalized_levenshtein_similarity(s1, s2):
    s1, s2 = str(s1).lower().strip(), str(s2).lower().strip()
    dist = Levenshtein.distance(s1, s2)
    max_len = max(len(s1), len(s2))
    if max_len == 0:
        return 1.0
    return 1 - (dist / max_len)

# Function to compute the similarity for a single row
def row_similarity(row):
    # Assume row['answers'] is a list of ground-truth strings
    ground_truths = row['answers']
    generated = row['generated_answer']
    # Compute similarity with each ground truth answer
    similarities = [normalized_levenshtein_similarity(gt, generated) for gt in ground_truths]
    # We take the maximum similarity (best match) as the score for that row.
    return max(similarities) if similarities else 0.0


# Compute similarity for each row
df["similarity"] = df.apply(row_similarity, axis=1)

# Calculate the average similarity (ANSL)
ansl_accuracy = df["similarity"].mean()

print("Row similarities:")
print(df[["answers", "generated_answer", "similarity"]])
print("Average Normalized Levenshtein Similarity (ANSL):", ansl_accuracy)